In [ ]:
# install
!pip install neologdn 'transformers[ja]' wandb

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.2/86.2 kB 3.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 20.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 600.9/600.9 kB 34.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.4/13.4 MB 66.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 47.4/47.4 MB 35.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.6/2.6 MB 67.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 71.8/71.8 MB 6.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.8/86.8 kB 13.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 195.4/195.4 kB 26.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 258.8/258.8 kB 30.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import torch
import json
import neologdn
import unicodedata
from torch.utils.data import Dataset, DataLoader
from transformers import AutoTokenizer, AutoModelForMaskedLM
from torch.optim import AdamW
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_recall_fscore_support
import numpy as np
import wandb
import random

In [ ]:
class DataPreprocessor:
    def __init__(self, file_path, tokenizer_name="tohoku-nlp/bert-base-japanese-whole-word-masking", max_length=512, batch_size=32, test_size=0.2):
        self.file_path = file_path
        self.tokenizer_name = tokenizer_name
        self.max_length = max_length
        self.batch_size = batch_size
        self.test_size = test_size
        self.tokenizer = AutoTokenizer.from_pretrained(tokenizer_name)
        self.train_dataloader, self.test_dataloader = self.prepare_data()

    def cleaning_text(self, text):
        normalized = neologdn.normalize(text)
        cleaned_text = unicodedata.normalize("NFKC", normalized)
        return cleaned_text

    def load_data(self):
        with open(self.file_path, 'r', encoding='utf-8') as file:
            data = json.load(file)
            cleaned_data = [self.cleaning_text(text) for text in data]
        return cleaned_data

    def split_data(self, data):
        data_pairs = [(data[i], data[i + 1]) for i in range(0, len(data) - 1, 2)]
        train_pairs, test_pairs = train_test_split(data_pairs, test_size=self.test_size, random_state=42)
        return train_pairs, test_pairs

    def create_data_loader(self, text_pairs):
        dataset = BERTDataset(text_pairs, self.tokenizer, max_length=self.max_length)
        dataloader = DataLoader(dataset, batch_size=self.batch_size, shuffle=True)
        return dataloader

    def prepare_data(self):
        data = self.load_data()
        train_pairs, test_pairs = self.split_data(data)
        train_dataloader = self.create_data_loader(train_pairs)
        test_dataloader = self.create_data_loader(test_pairs)
        return train_dataloader, test_dataloader

class BERTDataset(Dataset):
    def __init__(self, texts, tokenizer, max_length=512, mlm_probability=0.15):
        self.texts = texts
        self.tokenizer = tokenizer
        self.max_length = max_length
        self.mlm_probability = mlm_probability
        self.vocab_items = list(tokenizer.vocab.items())

    def __len__(self):
        return len(self.texts)

    def random_masking(self, tokens):
        labels = [-100] * len(tokens)  # ラベルの初期化
        masked_tokens = tokens.clone()  # トークン列のディープコピーを作成
        for i, token_id in enumerate(tokens.tolist()):  # tokensをリストに変換してイテレート
            # 特殊トークンとマスクトークンはスキップ
            if token_id in self.tokenizer.all_special_ids:
                continue
            # ランダムにトークンをマスクする条件
            if random.random() < self.mlm_probability:
                labels[i] = token_id  # 元のトークンIDをラベルに設定
                prob = random.random()
                if prob < 0.8:
                    # 80%の確率でマスクトークンに置き換え
                    masked_tokens[i] = self.tokenizer.mask_token_id
                elif prob < 0.9:
                    # 10%の確率でランダムなトークンに置き換え
                    random_token_id = random.choice(list(self.tokenizer.vocab.values()))
                    masked_tokens[i] = random_token_id
                # 10%の確率で元のトークンをそのまま使用する場合は、masked_tokens[i]を更新する必要がない
            # マスクしない場合も、masked_tokens[i]を更新する必要がない
        return masked_tokens, labels




    def __getitem__(self, idx):
        text1, text2 = self.texts[idx]
        tokens = self.tokenizer(text1, text2, truncation="longest_first", max_length=self.max_length, return_tensors="pt", padding="max_length")
        input_ids = tokens["input_ids"][0]
        token_type_ids = tokens["token_type_ids"][0]
        attention_mask = tokens["attention_mask"][0]
        tokens, labels = self.random_masking(input_ids)
        return torch.tensor(tokens), torch.tensor(labels), torch.tensor(attention_mask), torch.tensor(token_type_ids)

def compute_metrics(pred_labels, true_labels):
    precision, recall, f1, _ = precision_recall_fscore_support(true_labels, pred_labels, average='binary')
    accuracy = accuracy_score(true_labels, pred_labels)
    return accuracy, precision, recall, f1

def compute_perplexity(loss):
    return np.exp(loss)

def evaluate(model, dataloader, device):
    model.eval()
    total_loss = 0
    preds, labels = [], []

    with torch.no_grad():
        for batch in dataloader:
            inputs, labels_batch, attention_mask, token_type_ids = batch
            inputs, labels_batch, attention_mask, token_type_ids = inputs.to(device), labels_batch.to(device), attention_mask.to(device), token_type_ids.to(device)

            outputs = model(input_ids=inputs, attention_mask=attention_mask, token_type_ids=token_type_ids, labels=labels_batch)
            loss = outputs.loss
            total_loss += loss.item()

            logits = outputs.logits
            preds.extend(torch.argmax(logits, dim=-1).cpu().numpy())
            labels.extend(labels_batch.cpu().numpy())

    avg_loss = total_loss / len(dataloader)
    perplexity = compute_perplexity(avg_loss)
    return avg_loss, perplexity

def train(model, train_dataloader, optimizer, device, epochs=4):
    for epoch in range(epochs):
        model.train()
        total_loss = 0
        for batch in train_dataloader:
            inputs, labels, attention_mask, token_type_ids = batch
            inputs, labels, attention_mask, token_type_ids = inputs.to(device), labels.to(device), attention_mask.to(device), token_type_ids.to(device)

            optimizer.zero_grad()
            outputs = model(input_ids=inputs, attention_mask=attention_mask, token_type_ids=token_type_ids, labels=labels)
            loss = outputs.loss
            loss.backward()
            optimizer.step()
            total_loss += loss.item()

            # WandB logging
            wandb.log({
                "train_loss": loss.item(),
            })
            print(f"Epoch: {epoch}, Train Loss: {loss.item()}")

        avg_loss = total_loss / len(train_dataloader)
        perplexity = compute_perplexity(avg_loss)


        wandb.log({
            "train_loss": avg_loss,
            "train_perplexity": perplexity
        })
        print(f"Epoch: {epoch}, Train Loss: {avg_loss}, Train Perplexity: {perplexity}")


In [ ]:

wandb.login()
wandb.init(project="Continual Pretraining of BERT on Legal Domain For all sentence", config={
    "epochs": 2,
    "learning_rate": 1e-4,
    "batch_size": 13,
    "max_length": 512,
    "mlm_probability": 0.15
})
config = wandb.config  # Access the configuration settings via wandb.config

bs = config["batch_size"]
lr = config["learning_rate"]
epochs = config["epochs"]
max_length = config["max_length"]
# DataPreprocessorの初期化と設定

data_preprocessor = DataPreprocessor(file_path="/content/drive/MyDrive/corpus_Pretraing_400.json", max_length=max_length, batch_size=bs)

<IPython.core.display.Javascript object>

wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: xiangchitian26. Use `wandb login --relogin` to force relogin


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/120 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/479 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/258k [00:00<?, ?B/s]

In [ ]:
# モデル、オプティマイザーの初期化
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = AutoModelForMaskedLM.from_pretrained("tohoku-nlp/bert-base-japanese-whole-word-masking").to(device)
optimizer = AdamW(model.parameters(), lr=lr)

# 訓練と評価の実行
train(model, data_preprocessor.train_dataloader, optimizer, device, epochs=epochs)
wandb.save("model.pt")
model.save_pretrained("model.pt")
wandb.finish()


pytorch_model.bin:   0%|          | 0.00/445M [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/torch/_utils.py:831: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()
Some weights of the model checkpoint at tohoku-nlp/bert-base-japanese-whole-word-masking were not used when initializing BertForMaskedLM: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exact

Epoch: 0, Train Loss: 2.431859254837036
Epoch: 0, Train Loss: 1.996899962425232
Epoch: 0, Train Loss: 1.9113715887069702
Epoch: 0, Train Loss: 1.6816939115524292
Epoch: 0, Train Loss: 1.8227672576904297
Epoch: 0, Train Loss: 2.305180072784424
Epoch: 0, Train Loss: 2.02392315864563
Epoch: 0, Train Loss: 1.878844141960144
Epoch: 0, Train Loss: 1.704481601715088
Epoch: 0, Train Loss: 1.647470235824585
Epoch: 0, Train Loss: 1.9806363582611084
Epoch: 0, Train Loss: 1.8009886741638184
Epoch: 0, Train Loss: 1.5992401838302612
Epoch: 0, Train Loss: 2.3208019733428955
Epoch: 0, Train Loss: 2.5154879093170166
Epoch: 0, Train Loss: 1.9381310939788818
Epoch: 0, Train Loss: 2.2130324840545654
Epoch: 0, Train Loss: 2.082097291946411
Epoch: 0, Train Loss: 1.9919264316558838
Epoch: 0, Train Loss: 1.7295446395874023
Epoch: 0, Train Loss: 2.304593086242676
Epoch: 0, Train Loss: 1.7757214307785034
Epoch: 0, Train Loss: 1.9914647340774536
Epoch: 0, Train Loss: 2.1206085681915283
Epoch: 0, Train Loss: 1.78

Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.


Epoch: 0, Train Loss: 1.3969547748565674
Epoch: 0, Train Loss: 2.20181941986084
Epoch: 0, Train Loss: 1.6054140329360962
Epoch: 0, Train Loss: 1.876668930053711
Epoch: 0, Train Loss: 1.5826747417449951
Epoch: 0, Train Loss: 1.5433157682418823
Epoch: 0, Train Loss: 1.6494665145874023
Epoch: 0, Train Loss: 1.4434504508972168
Epoch: 0, Train Loss: 2.038516044616699
Epoch: 0, Train Loss: 1.6606464385986328
Epoch: 0, Train Loss: 1.5433472394943237
Epoch: 0, Train Loss: 1.6799206733703613
Epoch: 0, Train Loss: 1.2732597589492798
Epoch: 0, Train Loss: 1.3617662191390991
Epoch: 0, Train Loss: 1.5200047492980957
Epoch: 0, Train Loss: 1.5704904794692993
Epoch: 0, Train Loss: 1.7868998050689697
Epoch: 0, Train Loss: 1.5912582874298096
Epoch: 0, Train Loss: 1.5575876235961914
Epoch: 0, Train Loss: 1.4394185543060303
Epoch: 0, Train Loss: 1.5194510221481323
Epoch: 0, Train Loss: 1.5270079374313354
Epoch: 0, Train Loss: 1.507008671760559
Epoch: 0, Train Loss: 1.6898456811904907
Epoch: 0, Train Loss:

...

Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.


Epoch: 0, Train Loss: 1.0037522315979004
Epoch: 0, Train Loss: 1.1667513847351074
Epoch: 0, Train Loss: 1.2893879413604736
Epoch: 0, Train Loss: 1.4405922889709473
Epoch: 0, Train Loss: 1.6974766254425049
Epoch: 0, Train Loss: 1.3640657663345337
Epoch: 0, Train Loss: 1.4603956937789917
Epoch: 0, Train Loss: 1.4032021760940552
Epoch: 0, Train Loss: 1.5702691078186035
Epoch: 0, Train Loss: 1.6248087882995605
Epoch: 0, Train Loss: 1.945824384689331
Epoch: 0, Train Loss: 1.2825100421905518
Epoch: 0, Train Loss: 1.4793452024459839
Epoch: 0, Train Loss: 1.3476347923278809
Epoch: 0, Train Loss: 1.3323384523391724
Epoch: 0, Train Loss: 1.105773687362671
Epoch: 0, Train Loss: 1.2185465097427368
Epoch: 0, Train Loss: 1.0557578802108765
Epoch: 0, Train Loss: 1.6629867553710938
Epoch: 0, Train Loss: 1.6658215522766113
Epoch: 0, Train Loss: 1.3676106929779053
Epoch: 0, Train Loss: 1.4506596326828003
Epoch: 0, Train Loss: 1.5443657636642456
Epoch: 0, Train Loss: 1.4844647645950317
Epoch: 0, Train Lo

Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.


Epoch: 0, Train Loss: 1.445310115814209
Epoch: 0, Train Loss: 1.3765790462493896
Epoch: 0, Train Loss: 1.6581090688705444
Epoch: 0, Train Loss: 1.1082159280776978
Epoch: 0, Train Loss: 1.34280264377594
Epoch: 0, Train Loss: 1.514636754989624
Epoch: 0, Train Loss: 1.382891058921814
Epoch: 0, Train Loss: 1.0917034149169922
Epoch: 0, Train Loss: 1.5560190677642822
Epoch: 0, Train Loss: 1.4129784107208252
Epoch: 0, Train Loss: 1.2490909099578857
Epoch: 0, Train Loss: 1.5315498113632202
Epoch: 0, Train Loss: 1.242071509361267
Epoch: 0, Train Loss: 1.1823973655700684
Epoch: 0, Train Loss: 1.401228427886963
Epoch: 0, Train Loss: 1.656576156616211
Epoch: 0, Train Loss: 1.3525364398956299
Epoch: 0, Train Loss: 1.492348074913025
Epoch: 0, Train Loss: 1.4186252355575562
Epoch: 0, Train Loss: 1.7778105735778809
Epoch: 0, Train Loss: 1.2360248565673828
Epoch: 0, Train Loss: 1.5811011791229248
Epoch: 0, Train Loss: 1.2510806322097778
Epoch: 0, Train Loss: 1.235640048980713
Epoch: 0, Train Loss: 1.30

KeyboardInterrupt: 

### 850000件学習済み

In [ ]:
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Token: 
Add token as git credential? (Y/n) n
Token is valid (permission: write).
Your token has been saved to /root/.cache/huggingface/token
Login successful


In [ ]:
model.push_to_hub("SHONOSUKE/Addtional_Trained_BERT_For_Legal_Domain_v1")

model.safetensors:   0%|          | 0.00/443M [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/SHONOSUKE/Addtional_Trained_BERT_For_Legal_Domain_v1/commit/7219a4575f688c4d771699b138ed8b5e969631b6', commit_message='Upload BertForMaskedLM', commit_description='', oid='7219a4575f688c4d771699b138ed8b5e969631b6', pr_url=None, pr_revision=None, pr_num=None)

In [ ]:
model.save_pretrained("/content/drive/MyDrive/Addtional_Trained_BERT_For_Legal_Domain_v1")

In [ ]:
with open("/content/drive/MyDrive/Addtional_Trained_BERT_For_Legal_Domain_v1/dataset.json", "w") as f:
  json.dump(data_preprocessor.dataset, f)


In [ ]:
wandb.save("SHONOSUKE/Addtional_Trained_BERT_For_Legal_Domain_v1.safetensors")

[]

In [ ]:
wandb.finish()

AttributeError: 'BERTDataset' object has no attribute 'tensors'